In [1]:
from selenium import webdriver
import scrapy
import requests
from scrapy.http import TextResponse

In [2]:
!scrapy startproject wine_france

New Scrapy project 'wine_france', using template directory '/Users/myeongjinhong/anaconda3/lib/python3.7/site-packages/scrapy/templates/project', created in:
    /Users/myeongjinhong/Documents/notebook/wine/Crawling/wine_france

You can start your first spider with:
    cd wine_france
    scrapy genspider example example.com


In [3]:
!tree wine_france

wine_france
├── scrapy.cfg
└── wine_france
    ├── __init__.py
    ├── __pycache__
    ├── items.py
    ├── middlewares.py
    ├── pipelines.py
    ├── settings.py
    └── spiders
        ├── __init__.py
        └── __pycache__

4 directories, 7 files


In [4]:
%%writefile wine_france/wine_france/items.py
import scrapy

class CrawlerItem(scrapy.Item):
    title = scrapy.Field()
    o_price = scrapy.Field()
    s_price = scrapy.Field()
    points = scrapy.Field()
    variety = scrapy.Field()
    region = scrapy.Field()

Overwriting wine_france/wine_france/items.py


In [5]:
%%writefile wine_france/wine_france/spiders/spider.py
import scrapy
from wine_france.items import CrawlerItem
from selenium import webdriver

class FranceSpider(scrapy.Spider):
    
    name = "WineFrance"
    allow_domain = ["www.wine.com"]
    start_urls = ["https://www.wine.com/list/wine/france/7155-107033"]
    
    def parse(self, response):
        for page in range(1, 165):
            pages = "https://www.wine.com/list/wine/france/7155-107033/{}".format(page)
            yield scrapy.Request(pages, callback=self.parse_link)

            
    def parse_link(self, response):
        options = webdriver.ChromeOptions()
        options.add_argument("headless")
        driver = webdriver.Chrome(options=options)
        driver.get(response.url)
        elements = driver.find_elements_by_xpath('//*[@id="false"]/section[2]/ul/li/div/div[1]/a')
        links = [element.get_attribute("href") for element in elements]
        driver.quit()
        for link in links:
            link = response.urljoin(link)
            yield scrapy.Request(link, callback=self.parse_page_contents)
            
             
    def parse_page_contents(self, response):
        item = CrawlerItem()
        item['title'] = response.xpath('/html/body/div[7]/main/section[2]/div[2]/div[1]/h1/text()')[0].extract()
        item['points'] = response.xpath('/html/body/div[7]/main/section[3]/section[2]/div[1]/span[1]/text()')[0].extract()
        item['o_price'] = response.xpath('/html/body/div[7]/main/section[2]/div[2]/div[1]/div[3]/div[1]/div[2]/span[1]/text()')[0].extract()
        item['s_price'] = response.xpath('/html/body/div[7]/main/section[2]/div[2]/div[1]/div[3]/div[1]/div[3]/span[1]/text()')[0].extract()
        item['variety'] = response.xpath('/html/body/div[7]/main/section[2]/div[2]/div[1]/div[1]/span[1]/a/text()')[0].extract()
        item['region'] = response.xpath('/html/body/div[7]/main/section[2]/div[2]/div[1]/div[1]/span[2]/a/text()')[0].extract()
        yield item

Writing wine_france/wine_france/spiders/spider.py


In [6]:
!sed -i .bak 's/ROBOTSTXT_OBEY = True/ROBOTSTXT_OBEY = False/' wine_france/wine_france/settings.py


In [7]:
%%writefile run.sh
cd wine_france
scrapy crawl WineFrance -o WineFrance.csv

Overwriting run.sh


In [8]:
!source run.sh

2019-07-09 13:24:54 [scrapy.utils.log] INFO: Scrapy 1.6.0 started (bot: wine_france)
2019-07-09 13:24:54 [scrapy.utils.log] INFO: Versions: lxml 4.3.2.0, libxml2 2.9.9, cssselect 1.0.3, parsel 1.5.1, w3lib 1.20.0, Twisted 19.2.1, Python 3.7.3 (default, Mar 27 2019, 16:54:48) - [Clang 4.0.1 (tags/RELEASE_401/final)], pyOpenSSL 19.0.0 (OpenSSL 1.1.1b  26 Feb 2019), cryptography 2.6.1, Platform Darwin-18.6.0-x86_64-i386-64bit
2019-07-09 13:24:54 [scrapy.crawler] INFO: Overridden settings: {'BOT_NAME': 'wine_france', 'FEED_FORMAT': 'csv', 'FEED_URI': 'WineFrance.csv', 'NEWSPIDER_MODULE': 'wine_france.spiders', 'SPIDER_MODULES': ['wine_france.spiders']}
2019-07-09 13:24:54 [scrapy.extensions.telnet] INFO: Telnet Password: 13a82060fde82be1
2019-07-09 13:24:54 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.extensi

2019-07-09 13:25:03 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56387 "GET /session/bca087f88ac008684dd5fe1ca06d4d27/element/0.4267211970388456-15/attribute/href HTTP/1.1" 200 138
2019-07-09 13:25:03 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:03 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56387/session/bca087f88ac008684dd5fe1ca06d4d27/element/0.4267211970388456-16/attribute/href {"name": "href", "id": "0.4267211970388456-16", "sessionId": "bca087f88ac008684dd5fe1ca06d4d27"}
2019-07-09 13:25:03 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56387 "GET /session/bca087f88ac008684dd5fe1ca06d4d27/element/0.4267211970388456-16/attribute/href HTTP/1.1" 200 164
2019-07-09 13:25:03 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:03 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56387/session/bca087f88ac008684dd5fe1ca06d4d27/element/0.4267211970388456

2019-07-09 13:25:05 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56429 "POST /session HTTP/1.1" 200 1014
2019-07-09 13:25:05 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:05 [selenium.webdriver.remote.remote_connection] DEBUG: POST http://127.0.0.1:56429/session/e57d739d8853ead585e2a608c8741042/url {"url": "https://www.wine.com/list/wine/france/7155-107033/35", "sessionId": "e57d739d8853ead585e2a608c8741042"}
2019-07-09 13:25:07 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56429 "POST /session/e57d739d8853ead585e2a608c8741042/url HTTP/1.1" 200 72
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: POST http://127.0.0.1:56429/session/e57d739d8853ead585e2a608c8741042/elements {"using": "xpath", "value": "//*[@id=\"false\"]/section[2]/ul/li/div/div[1]/a", "sessionId": "e57d739d8853ead585e2a608c8741042"}
2019-07-09 13:25:07 [urllib3

2019-07-09 13:25:07 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56429 "GET /session/e57d739d8853ead585e2a608c8741042/element/0.4163988293648029-16/attribute/href HTTP/1.1" 200 164
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56429/session/e57d739d8853ead585e2a608c8741042/element/0.4163988293648029-17/attribute/href {"name": "href", "id": "0.4163988293648029-17", "sessionId": "e57d739d8853ead585e2a608c8741042"}
2019-07-09 13:25:07 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56429 "GET /session/e57d739d8853ead585e2a608c8741042/element/0.4163988293648029-17/attribute/href HTTP/1.1" 200 153
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:07 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56429/session/e57d739d8853ead585e2a608c8741042/element/0.4163988293648029

2019-07-09 13:25:10 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56478 "GET /session/fd8d231ea6b58e7bd12f061caa037fed/element/0.31366433523789894-3/attribute/href HTTP/1.1" 200 154
2019-07-09 13:25:10 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:10 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56478/session/fd8d231ea6b58e7bd12f061caa037fed/element/0.31366433523789894-4/attribute/href {"name": "href", "id": "0.31366433523789894-4", "sessionId": "fd8d231ea6b58e7bd12f061caa037fed"}
2019-07-09 13:25:10 [urllib3.connectionpool] DEBUG: http://127.0.0.1:56478 "GET /session/fd8d231ea6b58e7bd12f061caa037fed/element/0.31366433523789894-4/attribute/href HTTP/1.1" 200 159
2019-07-09 13:25:10 [selenium.webdriver.remote.remote_connection] DEBUG: Finished Request
2019-07-09 13:25:10 [selenium.webdriver.remote.remote_connection] DEBUG: GET http://127.0.0.1:56478/session/fd8d231ea6b58e7bd12f061caa037fed/element/0.3136643352378989

...

2019-07-09 13:52:14 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/clos-des-lunes-lune-dargent-2016/202555> (referer: https://www.wine.com/list/wine/france/7155-107033/9)
2019-07-09 13:52:14 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/bouchard-pere-and-fils-cote-de-beaune-villages-2014/234172> from <GET https://www.wine.com/product/Bouchard-Pere-and-Fils-Cote-de-Beaune-Villages-2014/234172>
2019-07-09 13:52:14 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/luc-belaire-rare-rose/123420> from <GET https://www.wine.com/product/Luc-Belaire-Rare-Rose/123420>
2019-07-09 13:52:14 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/chateau-duhart-milon-2009/111781>
{'o_price': '150',
 'points': '4.2',
 'region': 'Pauillac, Bordeaux, France',
 's_price': '139',
 'title': 'Chateau Duhart-Milon 2009',
 'variety': 'Bordeaux Red Blends

2019-07-09 13:52:16 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/chateau-de-pibarnon-bandol-rouge-2016/530510>
{'o_price': '49',
 'points': '0.0',
 'region': 'Bandol, Provence, France',
 's_price': '49',
 'title': 'Chateau de Pibarnon Bandol Rouge 2016',
 'variety': 'Mourvedre'}
2019-07-09 13:52:16 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/bouchard-pere-and-fils-cote-de-beaune-villages-2014/234172> (referer: https://www.wine.com/list/wine/france/7155-107033/12)
2019-07-09 13:52:16 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/domaines-barons-de-rothschild-legende-bordeaux-blanc-2017/430811> (referer: https://www.wine.com/list/wine/france/7155-107033/12)
2019-07-09 13:52:16 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/chateau-dyquem-sauternes-slightly-torn-label-1989/6411> (referer: https://www.wine.com/list/wine/france/7155-107033/12)
2019-07-09 13:52:16 [scrapy

2019-07-09 13:52:17 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/chateau-branaire-ducru-futures-pre-sale-2018/520383> from <GET https://www.wine.com/product/Chateau-Branaire-Ducru-Futures-Pre-Sale-2018/520383>
2019-07-09 13:52:17 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/chateau-minuty-rose-et-or-2017/485083>
{'o_price': '37',
 'points': '0.0',
 'region': 'Cotes de Provence, Provence, France',
 's_price': '37',
 'title': 'Chateau Minuty Rose et Or 2017',
 'variety': 'Rosé'}
2019-07-09 13:52:17 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/chateau-la-fleur-petrus-2016/275656>
{'o_price': '239',
 'points': '4.5',
 'region': 'Pomerol, Bordeaux, France',
 's_price': '239',
 'title': 'Chateau La Fleur-Petrus 2016',
 'variety': 'Bordeaux Red Blends'}
2019-07-09 13:52:17 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/chateau-la-vieille-cure-futu

2019-07-09 13:52:19 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/commanderie-de-la-bargemone-coteaux-daix-en-provence-rose-2017/410463> from <GET https://www.wine.com/product/Commanderie-de-la-Bargemone-Coteaux-dAix-en-Provence-Rose-2017/410463>
2019-07-09 13:52:19 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/chateau-branaire-ducru-futures-pre-sale-2018/520383> (referer: https://www.wine.com/list/wine/france/7155-107033/15)
2019-07-09 13:52:19 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/chateau-le-temple-2015/400835> from <GET https://www.wine.com/product/Chateau-Le-Temple-2015/400835>
2019-07-09 13:52:19 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/chateau-branaire-ducru-futures-pre-sale-2018/520383>
{'o_price': '54',
 'points': '0.0',
 'region': 'St-Julien, Bordeaux, France',
 's_price': '54',
 'title': 'Chate

2019-07-09 13:52:20 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/gerard-bertrand-cuvee-thomas-jefferson-cremant-de-limoux-brut-rose-2016/513557> from <GET https://www.wine.com/product/Gerard-Bertrand-Cuvee-Thomas-Jefferson-Cremant-de-Limoux-Brut-Rose-2016/513557>
2019-07-09 13:52:20 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.wine.com/product/maison-lenvoye-bourgogne-blanc-2015/524119>
{'o_price': '20',
 'points': '0.0',
 'region': 'Burgundy, France',
 's_price': '20',
 'title': "Maison L'Envoye Bourgogne Blanc 2015",
 'variety': 'Chardonnay'}
2019-07-09 13:52:20 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.wine.com/product/chateau-figeac-2016/202343> from <GET https://www.wine.com/product/Chateau-Figeac-2016/202343>
2019-07-09 13:52:20 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.wine.com/product/chateau-le-temple-2015/400835> (referer: https://www.wine.com/lis

In [10]:
crawl_france= pd.read_csv("wine_france/wineFrance.csv")
crawl_france.tail()

o_price  points                                             region  \
3933      89     0.0                 Chateauneuf-du-Pape, Rhone, France   
3934      53     4.6                                  Champagne, France   
3935     249     4.4                      St. Emilion, Bordeaux, France   
3936      19     4.7  Cremant de Limoux, Limoux, Languedoc-Roussillo...   
3937      13     3.9                                             France   

     s_price                                              title  \
3933      89  Clos du Caillou Chateauneuf-du-Pape Les Quartz...   
3934      53                     Moet & Chandon Nectar Imperial   
3935     249                                Chateau Figeac 2016   
3936      19  Gerard Bertrand Cuvee Thomas Jefferson Cremant...   
3937       9  Charles de Fere Cuvee Jean-Louis Blanc de Blan...   

                         variety  
3933            Rhone Red Blends  
3934  Non-Vintage Sparkling Wine  
3935         Bordeaux Red Blends  
3936         Rosé Sparkling Wine  
3937  Non-Vintage Sparkling Wine

In [11]:
crawl_france.region.unique()

array(['Burgundy, France', 'Beaujolais, Burgundy, France',
       'Languedoc-Roussillon, France', 'St. Emilion, Bordeaux, France',
       "Pommard, Cote de Beaune, Cote d'Or, Burgundy, France",
       'Chateauneuf-du-Pape, Rhone, France', 'Margaux, Bordeaux, France',
       'Chablis, Burgundy, France', 'Cotes du Rhone, Rhone, France',
       'Pouilly-Loche, Maconnais, Burgundy, France', 'Rhone, France',
       'Pauillac, Bordeaux, France',
       "Vosne-Romanee, Cote de Nuits, Cote d'Or, Burgundy, France",
       "Chambolle-Musigny, Cote de Nuits, Cote d'Or, Burgundy, France",
       'Cotes de Provence, Provence, France', 'Champagne, France',
       "Gevrey-Chambertin, Cote de Nuits, Cote d'Or, Burgundy, France",
       'Minervois, Languedoc-Roussillon, France',
       'Vouvray, Touraine, Loire, France',
       "Morey-St-Denis, Cote de Nuits, Cote d'Or, Burgundy, France",
       'Pessac-Leognan, Bordeaux, France', 'Fronsac, Bordeaux, France',
       "Puligny-Montrachet, Cote de Beaune,